# Front End for Mobile PT Notebook Interface

In [4]:
# General imports
import cv2
import mediapipe as mp
import numpy as np
import os
import sys
from datetime import datetime, date
import time
import uuid
import seaborn as sns
import matplotlib.pyplot as plt
import pprint


# data processing and visualization helper functions
from processing import process_image, process_video
from data_acquisition import capture_session, test_fps_webcam
from visualization import plot_ROM_dtw_comparisons, calc_DTW_joints_metrics, create_3D_keypoints_video, plot_ex_animation
import visualization

# Request handling and data payload packaging
from django.core.serializers.json import DjangoJSONEncoder
import json
import requests

# DTW imports
from dtw import *

## Upload reference session

### 1. Simple script to get fps of webcam, camera

In [6]:
test_fps_webcam(webcam = 0)

Frames per second using video.get(cv2.CAP_PROP_FPS) : 30.0
Capturing 300 frames
Estimated frame rate: 29.04


### 2. Record reference video and image

In [5]:
# Delete temp reference video file if already exists
if os.path.exists("./tmp_reference.m4v"):
  os.remove("./tmp_reference.m4v")
else:
  print("The file does not exist")

# Delete reference image file if already exists
if os.path.exists("./tmp_reference.jpg"):
  os.remove("./tmp_reference.jpg")
else:
  print("The file does not exist")

Capture an image and video from opencv with a countdown and a timer

In [8]:
image_path, video_path = capture_session('tmp_reference', 10, 12, base_dir='./', webcam=0)

### 3. Run BP Pose Stimation on tmp image and video

In [7]:
flag, image_output = process_image(image_path)

flag, video_output = process_video(video_path)

INFO: Created TensorFlow Lite XNNPACK delegate for CPU.


### 4. Prepare data payload

In [8]:
# Choices stored in the backend
EXERCISE_CHOICES = [('SQUAT', 'SQUAT'),
               ('ARM_RAISE','ARM RAISE'),
               ('LEG_RAISE', 'LEG RAISE'),
               ('BICEP_CURL','BICEP CURL ALTERNATING'),]

In [9]:
exercise = 'SQUAT'
date = datetime.now()
default_name = f"{exercise}_{date.isoformat()}"

In [10]:
# payload is essentially an incomplete object for the Ref Session model
payload = {'exercise': exercise,
           'target_reps': 6,
           'name': default_name,
           'date': date,
           'pose_keypoints': image_output,
           'keypoints_sequence': video_output}

### 5. Send request

In [11]:
ref_url = 'http://127.0.0.1:8000/api/v1/reference_sessions/'

r = requests.post(ref_url, data=json.dumps(payload, cls=DjangoJSONEncoder), headers={'Content-Type': 'application/json'})
r.raise_for_status()

In [12]:
ex_details = r.json()

In [ ]:
visualization.plot_joint_angles(ex_details)

## Delete all reference sessions

In [5]:
# Delete all reference sessions
ref_url = 'http://127.0.0.1:8000/api/v1/reference_sessions/'

r = requests.delete(ref_url)
r.raise_for_status()

## Get all reference session data

In [ ]:
# Delete all reference sessions
ref_url = 'http://127.0.0.1:8000/api/v1/reference_sessions/'

r = requests.get(ref_url)
r.raise_for_status()

In [ ]:
refs = r.json()

for ref in refs:
    print(ref['id'])

## Upload Exercise Session

### 1. Record temp exercise session image and video

In [ ]:
name = 'tmp_exercise'

# Delete temp reference video file if already exists
if os.path.exists(f"./{name}.m4v"):
  os.remove(f"./{name}.m4v")
else:
  print("The file does not exist")

# Delete reference image file if already exists
if os.path.exists(f"./{name}.jpg"):
  os.remove(f"./{name}.jpg")
else:
  print("The file does not exist")

In [ ]:
# capture webcam image and video using opencv
capture_session(name,10,20, webcam=1)

### 2. Run BP on image and video

In [ ]:
name = 'squat_diff_angle'

In [ ]:
# Run BP on video and image frame
flag, image_output = process_image(f'./{name}.jpg')

flag, video_output = process_video(f'./{name}.m4v')

### 3. Prep payload 

In [ ]:
exercise = 'SQUAT'
date = datetime(2022, 12, 1)
default_name = f"{exercise}_{datetime(2022, 12, 1).isoformat()}"

# payload is essentially an incomplete object for the Ref Session model
payload = {'exercise': exercise,
           'target_reps': 5,
           'sets': 1,
           'name': name,
           'date': date,
           'reference': 'fa0401d0-9965-4dab-a4b1-37da20bd4f57',
           'pose_keypoints': image_output,
           'keypoints_sequence': video_output}

### 4. Submit request

In [ ]:
url = 'http://127.0.0.1:8000/api/v1/exercise_sessions/'

r = requests.post(url, data=json.dumps(payload, cls=DjangoJSONEncoder), headers={'Content-Type': 'application/json'})
r.raise_for_status()

## Delete All Exercises

Only do this if you're actually sure 

In [9]:
url = 'http://127.0.0.1:8000/api/v1/exercise_sessions/'

r = requests.delete(url)

# Animate Exercise Session

In [4]:
# Get all exercise data 
ex_url = 'http://127.0.0.1:8000/api/v1/exercise_sessions/'
ref_url = 'http://127.0.0.1:8000/api/v1/reference_sessions/'

pp = pprint.PrettyPrinter(indent=4, sort_dicts=True)

r = requests.get(ex_url)

ex_sessions = r.json()


In [3]:
from visualization import plot_ex_animation

plot_ex_animation(ex_sessions[0])

# Analyze DTW Results on Exercise Sessions

In [ ]:
EXERCISE_JOINTS = {'SQUAT': ['L_KNEE', 'R_KNEE', 'L_HIP','R_HIP'],
                     'ARM_RAISE': ['L_SHOULDER','R_SHOULDER'],
                     'LEG_RAISE': ['L_HIP','R_HIP'],
                     'BICEP_CURL':['L_ELBOW','R_ELBOW']}

ALL_JOINTS = ['L_KNEE', 'R_KNEE', 'L_HIP', 'R_HIP', 'L_ELBOW', 'R_ELBOW', 
              'L_SHOULDER', 'R_SHOULDER']

Get the data for the exercises and their references

1. Plot comparison joint angle graphs between ex and ref
2. compute DTW distances for individual joint signals

In [ ]:
# Get all exercise data 
ex_url = 'http://127.0.0.1:8000/api/v1/exercise_sessions/'
ref_url = 'http://127.0.0.1:8000/api/v1/reference_sessions/'

pp = pprint.PrettyPrinter(indent=4, sort_dicts=True)

r = requests.get(ex_url)

ex_sessions = r.json()

pairs = []

for ex_session in ex_sessions:
    ref_id  = ex_session['reference']
    r = requests.get(ref_url+ref_id)
    ref_data = r.json()

    pairs.append((ex_session, ref_data))

Temporary write data to a json file

In [ ]:
ex_data, ref_data = pairs[1]
plot_ROM_dtw_comparisons(ex_data, ref_data)
dtw_results = calc_DTW_joints_metrics(ex_data, ref_data)

pp.pprint(ex_data['name'])
pp.pprint(dtw_results)

In [ ]:
ex_data, ref_data = pairs[3]
plot_ROM_dtw_comparisons(ex_data, ref_data)
dtw_results = calc_DTW_joints_metrics(ex_data, ref_data)

pp.pprint(ex_data['name'])
pp.pprint(dtw_results)

# DTW Plot for Paper

In [2]:
ex_url = 'http://127.0.0.1:8000/api/v1/exercise_sessions/'
ref_url = 'http://127.0.0.1:8000/api/v1/reference_sessions/'

ref_id = '5f813a8a-53fa-4a47-a5f0-2826c2b3f73d'

# Get reference of particular id
r = requests.get(ref_url+ref_id)
ref_data = r.json()

In [3]:
# Get exercises that have reference
r = requests.get(ex_url, params={'reference_id': ref_id})

ex_data = r.json()

In [4]:
for ex in ex_data:
    print(ex['id'])

d2bb7d9d-99b9-4177-82b2-97afdadfa424
9ed9821a-4545-40be-bdf7-f8cdce43f312
df0aca3a-e61c-4cdc-8803-1f91c9015343
64a01e70-9bef-4790-a48b-61a48763ad56
4f3ce5f3-b8bb-46e4-9820-4a83ee380697


In [ ]:
pairs = [(ex, ref_data) for ex in ex_data]
ex_data, ref_data = pairs[0]
plot_ROM_dtw_comparisons(ex_data, ref_data)